#  Transforming Collections Data to Linked Art - Cleveland Museum of Art

## Introduction

[Linked Art](https://linked.art) is a community working together to create a shared Model based on Linked Open Data to describe Art. A number of exemplars will be published to demonstrate the processes involved in producing Linked Art JSON-LD, and also the potential applications of Linked Art, on the theme of:
- `Transformation` - Documented transformation process - using code, documentation and possibly visualisation
- `Reconciliation` - Documented reconciliation process - matching data with an external identifier source
- `Visualisation` - Documented transformation of Linked Art JSON-LD to data visualisation

This exemplar is concerned with `Transformation` - the transformation process, from collections data to Linked Art JSON-LD.

## Aim of the Notebook
The aim of the notebook is to demonstrate how easy it is to transform collections data to Linked Art JSON-LD.
## How
The notebook provides a documented, interactive code example of the transformation process, from collections data to Linked Art using data from the Cleveland Museum of Art (CMA). 

## Input Data
The input data file is from https://github.com/ClevelandMuseumArt/openaccess

## Attribution

- The Linked Art data model documentation has been sourced from the [Linked Art website](https://linked.art)

## Transformation Steps

### 1. Import What We Need for Notebook
- Import Python libraries

In [42]:
try:
    import ipywidgets as widgets
except:
    !pip install ipywidgets
    import ipywidgets as widgets

from ipywidgets import Layout
from ipywidgets import FileUpload

try:
    import IPython
except:
    !pip install IPython
    import IPython   
    
from IPython.display import display
from IPython.core.display import HTML
from IPython.display import IFrame

   
try:
    import xmltodict
except:
    !pip install xmltodict
    import xmltodict

try:
    import json
except:
    !pip install json
    import json 
    
    

try:
    import requests
except:
    !pip install requests
    import requests

        
#  baseURI for JSON-LD document
baseURI = "https://clevelandart.org/art/"


### 2. Parse CSV File

In [43]:
import csv

file = './data/cma/input/data.csv'

#remove BOM
s = open(file, mode='r', encoding='utf-8-sig').read()
open(file, mode='w', encoding='utf-8').write(s)

allObjects = csv.DictReader(open(file, mode='r',encoding='utf-8'))

all_linkedart = {}
    

In [44]:
def getObjDesc(obj, functionCall):
    
    desc = {}
    id = obj["id"]
    irn = obj["accession_number"]
    department  = obj["department"]
    title = obj["title"]
    datecreated = obj["creation_date"]
    medium = obj["support_materials"]
    classification = obj["type"]
    attribution = obj["creators"]
    credit_line = obj["creators"]
    titAccessionNo = obj["accession_number"]
    provenance = obj["provenance"]
    earliestdate = obj["creation_date_earliest"] 
    latestdate = obj["creation_date_latest"]
    
    if functionCall == "member":
        desc = objMember(obj,baseURI,PhyCollectionArea)
    if functionCall == "custody":
        desc = objCustody(TitObjectStatus)
    if functionCall == "owner":
        desc = objOwner(obj,baseURI,irn,TitAccessionDate,TitObjectStatus)
    if functionCall == "production":
        desc = objProd(obj, baseURI,irn, earliestdate,latestdate,datecreated)
    if functionCall == "core":
        desc = objCore(obj,baseURI,irn,title) 
    if functionCall == "id":
        desc = objId(obj, baseURI, irn, titAccessionNo)
    if functionCall == "names":
        desc = objNames(obj, baseURI, irn, title)
    if functionCall == "class":
        if "titleObjectType" in vars():
            desc = objClass(obj, baseURI, irn, titleObjectType)
    if functionCall == "home":
            desc = objHome(obj,baseURI,irn)
    if functionCall == "location":
            desc = objLocation(obj,baseURI)
    if functionCall == "ling":
            desc = objLing(obj,baseURI,irn, credit_line, provenance)
    return desc

    
    
    

### 3. Data File as Python dictionary
The data file is converted to a Python dictionary, and will be used to transform the collection data for the artwork to JSON-LD. The following shows an example of a single artwork represented in the Python dictionary:

In [45]:
def getAllObjects(file):
    allObjects = csv.DictReader(open(file, mode='r',encoding='utf-8'))
    all = []
    for obj in allObjects:
        id = obj["id"]
        all.append(obj)  
    return all

allObjects = getAllObjects(file)

In [46]:
def objCore(obj, baseURI, irn, title):
    core = {}

        # minimum Linked Art properties
    core["@context"] = "https://linked.art/ns/v1/linked-art.json"
    core["id"] = baseURI + irn
    core["type"] = "HumanMadeObject"
    if "title" in vars():
        core["_label"] = title 
    
    return core

In [47]:
def objId(obj, baseURI, irn, titAccessionNo):
    artwork = {}       
    artwork["identified_by"] = []          
    if titAccessionNo != "":
        artwork["identified_by"].append({
        "id": baseURI + "object/" + irn + "/object-number",
        "type": "Identifier",
        "_label": "CMA Object Number for the Object",
        "content": titAccessionNo,
        "classified_as": [{
            "id": "http://vocab.getty.edu/aat/300312355",
            "type": "Type",
            "_label": "accession numbers"
                        }]
                })
        
    return artwork

In [48]:
def objNames(obj, baseURI, irn, title):

    artwork = {}
    artwork["identified_by"] = []
    
    artwork["identified_by"].append({
        "id": baseURI + "object/" + irn + "/title",
        "type": "Name",
        "_label": "Primary Title for the Object",
        "content": title ,
        "classified_as": [{
        "id": "http://vocab.getty.edu/aat/300404670",
        "type": "Type",
        "_label": "preferred terms"
                        }]
                })
    try:   
        if obj["table"]["@name"] == "AltTitles":
            x = 0
            for tuple in obj["table"]["tuple"]:
                x +=1
                for atom in tuple:
                    content = ""
                    if atom["@name"] == "TitAlternateTitles":
                        content = atom["#text"]
                        artwork["identified_by"].append({
                            "id": baseURI + "object/" + irn + "/alt-title-" + x,
                            "type": "Name",
                            "_label": "Alternate Title for the Object",
                            "content": content,
                            "classified_as": [{
                                "id": "http://vocab.getty.edu/aat/300417227",
                                "type": "Type",
                                "_label": "alternate titles"}]   
                        })
    except:
        pass

    return artwork

In [49]:
def objLing(obj, baseURI,irn, SumCreditLine, provenance):
    artwork = {}
    artwork["referred_to_by"] = []
    if SumCreditLine != "":
        artwork["referred_to_by"].append(
                {
                "id": baseURI + "object/" + irn + "/credit-line",
                "type": "LinguisticObject",
                "_label": "Credit Line for the Object",
                "content": SumCreditLine,
                "classified_as": [
                        {
                        "id": "http://vocab.getty.edu/aat/300026687",
                        "type": "Type",
                        "_label": "acknowledgments"
                        },
                        {
                        "id": "http://vocab.getty.edu/aat/300418049",
                        "type": "Type",
                        "_label": "brief texts"
                        }]
                })
              
    if provenance != "":
        artwork["referred_to_by"].append({
                "id": baseURI + "object/" + irn + "/provenance-statement",
                    "type": "LinguisticObject",
                    "_label": "Provenance Statement about the Object",
                    "content": provenance,
                    "classified_as": [
                        {
                            "id": "http://vocab.getty.edu/aat/300055863",
                            "type": "Type",
                            "_label": "provenance (history of ownership)"
                        },
                        {
                            "id": "http://vocab.getty.edu/aat/300418049",
                            "type": "Type",
                            "_label": "brief texts"
                        }
                    ]
            })
        
            
    return artwork

In [50]:
def objProd(obj, baseURI,irn, earliestdate,latestdate,datecreated):
    
    if "attribution" in list(obj.keys()):
        attr = obj["Attribution"]
    else:
        attr = ""
    
    artwork = {}
    
    #produced_by property
    artwork["produced_by"] = []
    artwork["produced_by"].append({
                 "id": baseURI + "object/" + irn + "/production",
                "type": "Production",
                "_label": "Production of the Object"})
    
    #carried_out_by property
    carried_out_by = []
    carried_out_by.append(
                                {
                                "id":  baseURI + "actor/" + irn,
                                "type": "Actor",
                                "_label": attr
                                }
                            )        
                                  
    if len(carried_out_by) > 0:
        artwork["produced_by"].append(
                    {
                    "carried_out_by": carried_out_by
                    })
                
    # timespan property
    timespan = False
    
    
    for date in (earliestdate,latestdate,datecreated):
        if date != "":
            timespan = True
            
    if timespan == True:
        #label
        label = "date unknown"
        if datecreated != "":
            label = datecreated
        elif (earliestdate != "") or (latestdate != ""):
            label = earliestdate + " - " + latestdate
        
        timespanObj = {
               "id": baseURI + irn + "/production/timespan",
                "type": "TimeSpan",
                "_label": label,
            }
        
        if earliestdate != "":
            timespanObj["begin_of_the_begin"] = earliestdate
    
        if latestdate != "":
            timespanObj["end_of_the_end"] = latestdate
        
        artwork["produced_by"].append({"timespan" : timespanObj}) 
        
    return artwork

In [51]:
def objCustody(TitObjectStatus):
    
    currentowner = False
    artwork = {}
    
    checkObjStatus = ('Accessioned','Partial Accession')
    for status in checkObjStatus:
        if status == TitObjectStatus:
            currentowner = True
    if 'IMA-Owned' in TitObjectStatus:
            currentowner = True
            
    if currentowner == False:  
        artwork["current_keeper"] =  {
                "id": "http://vocab.getty.edu/ulan/500300517",
                "type": "Group",
                "_label": "PMA",
                "classified_as": [
                    {
                        "id": "http://vocab.getty.edu/aat/300312281",
                        "type": "Type",
                        "_label": "museums (institutions)"
                    }]}
    
    return artwork

## 4. Build the Linked Art JSON-LD files <a id="build"/>

The following steps will transform the catalogue data for all of the artworks to Linked Art JSON-LD. 

In [57]:
file = './data/cma/input/data.csv'
allObjects = getAllObjects(file)

In [65]:
all_linkedart = {}

for obj in allObjects:
    irn = obj["id"]
    core = getObjDesc(obj, "core")
    all_linkedart[irn] = core 
    
    #identifiers
    id = getObjDesc(obj, "id")
    all_linkedart[irn].update(id)
    
    #names
    desc = getObjDesc(obj, "names")
    all_linkedart[irn].update(desc) 
    
    #classification
    desc = getObjDesc(obj, "class")
    if "classified_as" in list(desc.keys()):
        all_linkedart[irn].update(desc)
      
    # homepage
   # desc = getObjDesc(obj, "home")
   # all_linkedart[irn].update(desc) 
    
    # location
   # desc = getObjDesc(obj, "location")
   # all_linkedart[irn].update(desc) 
    
    # linguistic objects
    desc = getObjDesc(obj, "ling")
    all_linkedart[irn].update(desc) 
    
    # production
    desc = getObjDesc(obj, "production") 
    all_linkedart[irn].update(desc) 
    
    # ownership
   # desc = getObjDesc(obj, "owner")
   # all_linkedart[irn].update(desc)  
    
    #custody
   # desc = getObjDesc(obj, "custody")
   # if "current_keeper" in list(desc.keys()):
   #     all_linkedart[irn].update(desc)  
    
    # member 
  #  desc = getObjDesc(obj, "member")
  #  all_linkedart[irn].update(desc) 

### View the final Linked Art JSON-LD 

In [66]:
for id in all_linkedart:
    text_file = open("./data/cma/output/json/all/" + id + ".json", "w")
    n = text_file.write(json.dumps(all_linkedart[id], indent=2))
    text_file.close()

In [ ]:
import os
from IPython.core.display import display, HTML


def fn():       # 1.Get file names from directory
    file_list=os.listdir(r"./data/cma/output/json/all/")
   
    for file in file_list:
        display(HTML("<a href='./data/cma/output/json/all/" + file +"'>" + file + "</a>"))
    
fn()